from google.colab import drive

# Accessing My Google Drive
drive.mount('/content/drive')
datapath="drive/My Drive/MLVC_competition"

!unzip '/content/drive/MyDrive/MLVC_competition/dataset.zip'

# Define Model

In [2]:
import torch
print(torch.cuda.is_available())
print(torch.cuda.device_count())
print(torch.cuda.get_device_name(0)+'\n'+torch.cuda.get_device_name(1))
cuda=torch.device("cuda")

True
2
TITAN Xp
TITAN X (Pascal)


In [3]:

import torch.nn as nn
import torch.nn.functional as F

class LeNet_STL10(nn.Module):
    def __init__(self):
        super(LeNet_STL10, self).__init__()
        self.num_classes = 10

        self.relu = nn.ReLU(inplace=True)
        self.conv1 = nn.Conv2d(3, 6, kernel_size=5, stride=1)
        self.pool1 = nn.MaxPool2d((2, 2), stride=2)
        self.conv2 = nn.Conv2d(6, 16, kernel_size=5, stride=1)
        self.pool2 = nn.MaxPool2d((2, 2), stride=2)
        self.fc1 = nn.Linear(400, 120)
        self.fc2 = nn.Linear(120, 84)
        self.fc3 = nn.Linear(84, self.num_classes)

        for m in self.modules():
            if isinstance(m, nn.Conv2d):
                nn.init.kaiming_normal_(m.weight, mode='fan_out', nonlinearity='relu')

    def forward(self, x):
        x = self.relu(self.conv1(x))
        x = self.pool1(x)

        x = self.relu(self.conv2(x))
        x = self.pool2(x)
        x = torch.flatten(x, 1)

        x = self.relu(self.fc1(x))
        x = self.relu(self.fc2(x))
        x = self.fc3(x)

        return x


def Model():
    """Return your custom model
    """
    return LeNet_STL10()

In [4]:
'''ResNet in PyTorch.
For Pre-activation ResNet, see 'preact_resnet.py'.
Reference:
[1] Kaiming He, Xiangyu Zhang, Shaoqing Ren, Jian Sun
    Deep Residual Learning for Image Recognition. arXiv:1512.03385
'''



class BasicBlock(nn.Module):
    expansion = 1

    def __init__(self, in_planes, planes, stride=1):
        super(BasicBlock, self).__init__()
        self.conv1 = nn.Conv2d(
            in_planes, planes, kernel_size=3, stride=stride, padding=1, bias=False)
        self.bn1 = nn.BatchNorm2d(planes)
        self.conv2 = nn.Conv2d(planes, planes, kernel_size=3,
                               stride=1, padding=1, bias=False)
        self.bn2 = nn.BatchNorm2d(planes)

        self.shortcut = nn.Sequential()
        if stride != 1 or in_planes != self.expansion*planes:
            self.shortcut = nn.Sequential(
                nn.Conv2d(in_planes, self.expansion*planes,
                          kernel_size=1, stride=stride, bias=False),
                nn.BatchNorm2d(self.expansion*planes)
            )

    def forward(self, x):
        out = F.relu(self.bn1(self.conv1(x)))
        out = self.bn2(self.conv2(out))
        out += self.shortcut(x)
        out = F.relu(out)
        return out


class Bottleneck(nn.Module):
    expansion = 4

    def __init__(self, in_planes, planes, stride=1):
        super(Bottleneck, self).__init__()
        self.conv1 = nn.Conv2d(in_planes, planes, kernel_size=1, bias=False)
        self.bn1 = nn.BatchNorm2d(planes)
        self.conv2 = nn.Conv2d(planes, planes, kernel_size=3,
                               stride=stride, padding=1, bias=False)
        self.bn2 = nn.BatchNorm2d(planes)
        self.conv3 = nn.Conv2d(planes, self.expansion *
                               planes, kernel_size=1, bias=False)
        self.bn3 = nn.BatchNorm2d(self.expansion*planes)

        self.shortcut = nn.Sequential()
        if stride != 1 or in_planes != self.expansion*planes:
            self.shortcut = nn.Sequential(
                nn.Conv2d(in_planes, self.expansion*planes,
                          kernel_size=1, stride=stride, bias=False),
                nn.BatchNorm2d(self.expansion*planes)
            )

    def forward(self, x):
        out = F.relu(self.bn1(self.conv1(x)))
        out = F.relu(self.bn2(self.conv2(out)))
        out = self.bn3(self.conv3(out))
        out += self.shortcut(x)
        out = F.relu(out)
        return out


class ResNet(nn.Module):
    def __init__(self, block, num_blocks, num_classes=10):
        super(ResNet, self).__init__()
        self.in_planes = 64

        self.conv1 = nn.Conv2d(3, 64, kernel_size=3,
                               stride=1, padding=1, bias=False)
        self.bn1 = nn.BatchNorm2d(64)
        self.layer1 = self._make_layer(block, 64, num_blocks[0], stride=1)
        self.layer2 = self._make_layer(block, 128, num_blocks[1], stride=2)
        self.layer3 = self._make_layer(block, 256, num_blocks[2], stride=2)
        #self.layer4 = self._make_layer(block, 512, num_blocks[3], stride=2)
        self.linear = nn.Linear(1024, num_classes)
        #self.linear = nn.Linear(512*block.expansion, num_classes)

    def _make_layer(self, block, planes, num_blocks, stride):
        strides = [stride] + [1]*(num_blocks-1)
        layers = []
        for stride in strides:
            layers.append(block(self.in_planes, planes, stride))
            self.in_planes = planes * block.expansion
        return nn.Sequential(*layers)

    def forward(self, x):
        out = F.relu(self.bn1(self.conv1(x)))
        out = self.layer1(out)
        out = self.layer2(out)
        out = self.layer3(out)
        #out = self.layer4(out)
        out = F.avg_pool2d(out, 4)
        out = out.view(out.size(0), -1)
        #print(out.size())
        out = self.linear(out)
        return out


def ResNet18():
    return ResNet(BasicBlock, [2, 2, 1])


def ResNet34():
    return ResNet(BasicBlock, [3, 4, 6, 3])


def ResNet50():
    return ResNet(Bottleneck, [3, 4, 6, 3])


def ResNet101():
    return ResNet(Bottleneck, [3, 4, 23, 3])


def ResNet152():
    return ResNet(Bottleneck, [3, 8, 36, 3])


def test():
    net = ResNet18()
    y = net(torch.randn(1, 3, 32, 32))
    print(y.size())

# test()

In [5]:
model=ResNet18()
print(model)

ResNet(
  (conv1): Conv2d(3, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (layer1): Sequential(
    (0): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (shortcut): Sequential()
    )
    (1): BasicBlock(
      (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=

In [6]:
pytorch_total_params = sum(p.numel() for p in model.parameters())
print(pytorch_total_params)

1604682


# Utils

In [7]:
class AverageMeter(object):
    r"""Computes and stores the average and current value
    """
    def __init__(self, name, fmt=':f'):
        self.name = name
        self.fmt = fmt
        self.reset()

    def reset(self):
        self.val = 0
        self.avg = 0
        self.sum = 0
        self.count = 0

    def update(self, val, n=1):
        self.val = val
        self.sum += val * n
        self.count += n
        self.avg = self.sum / self.count

    def __str__(self):
        fmtstr = '{name} {val' + self.fmt + '} ({avg' + self.fmt + '})'
        return fmtstr.format(**self.__dict__)


class ProgressMeter(object):
    def __init__(self, num_batches, *meters, prefix=""):
        self.batch_fmtstr = self._get_batch_fmtstr(num_batches)
        self.meters = meters
        self.prefix = prefix

    def print(self, batch):
        entries = [self.prefix + self.batch_fmtstr.format(batch)]
        entries += [str(meter) for meter in self.meters]
        print('\t'.join(entries))

    def _get_batch_fmtstr(self, num_batches):
        num_digits = len(str(num_batches // 1))
        fmt = '{:' + str(num_digits) + 'd}'
        return '[' + fmt + '/' + fmt.format(num_batches) + ']'


def accuracy(output, target, topk=(1,)):
    r"""Computes the accuracy over the $k$ top predictions for the specified values of k
    """
    with torch.no_grad():
        maxk = max(topk)
        batch_size = target.size(0)

        # _, pred = output.topk(maxk, 1, True, True)
        # pred = pred.t()
        # correct = pred.eq(target.view(1, -1).expand_as(pred))

        # faster topk (ref: https://github.com/pytorch/pytorch/issues/22812)
        _, idx = output.sort(descending=True)
        pred = idx[:,:maxk]
        pred = pred.t()
        correct = pred.eq(target.view(1, -1).expand_as(pred))

        res = []

        for k in topk:
            correct_k = correct[:k].reshape(-1).float().sum(0, keepdim=True)
            res.append(correct_k.mul_(100.0 / batch_size))
        return res

#Hyperparameter

In [8]:
SAVEPATH = './weight/test/'
WEIGHTDECAY = 5e-4
MOMENTUM = 0.9
BATCHSIZE = 256
LR = 0.1
EPOCHS = 1000
PRINTFREQ = 10

#Train Model

In [ ]:
import time

import torch
import torch.nn as nn

import torchvision
import torchvision.transforms as transforms
from torch.utils.data import Dataset, DataLoader


def main():
   model = ResNet18()

   ##### optimizer / learning rate scheduler / criterion #####
   optimizer = torch.optim.SGD(model.parameters(), lr=LR,
                               momentum=MOMENTUM, weight_decay=WEIGHTDECAY,
                               nesterov=True)
   scheduler = torch.optim.lr_scheduler.MultiStepLR(optimizer, [100, 150],
                                                    gamma=0.1)
   criterion = torch.nn.CrossEntropyLoss()
   ###########################################################

   model = model.cuda()
   criterion = criterion.cuda()

   # Check number of parameters your model
   pytorch_total_params = sum(p.numel() for p in model.parameters())
   print(f"Number of parameters: {pytorch_total_params}")
   
   if int(pytorch_total_params) > 2000000:
       print('Your model has the number of parameters more than 2 millions..')
       return
   
   normalize = transforms.Normalize(mean=[0.485, 0.456, 0.406],
                                    std=[0.229, 0.224, 0.225])
   train_transform = transforms.Compose([
       transforms.RandomCrop(32, padding=4),
       transforms.RandomHorizontalFlip(),
       transforms.ToTensor(),
       normalize
   ])

   valid_transform = transforms.Compose([
       transforms.ToTensor(),
       normalize
   ])

   """
   train_dataset = torchvision.datasets.ImageFolder(
       '/home/dhk1349/Desktop/Machine Learning/train', transform=train_transform)
   train_loader = DataLoader(train_dataset,
                             batch_size=BATCHSIZE, shuffle=True,
                             num_workers=4, pin_memory=True)
   
   val_dataset = torchvision.datasets.ImageFolder('/home/dhk1349/Desktop/Machine Learning/valid', transform=valid_transform)
   val_loader = DataLoader(val_dataset, batch_size=BATCHSIZE, shuffle=True, num_workers=4, pin_memory=True)
   """

   trainset = torchvision.datasets.CIFAR10(root='/home/dhk1349/바탕화면/dataset/cifar10/', train=True,
                                        download=True, transform=train_transform)
   train_loader = torch.utils.data.DataLoader(trainset, batch_size=4,
                                          shuffle=True, num_workers=2)

   testset = torchvision.datasets.CIFAR10(root='/home/dhk1349/바탕화면/dataset/cifar10/', train=False,
                                       download=True, transform=train_transform)
   val_loader = torch.utils.data.DataLoader(testset, batch_size=4,
                                         shuffle=False, num_workers=2)
    
   last_top1_acc = 0

   # LOSS FOR EARLY STOPPING
   best_valid_loss = float('inf')
   early_stop_check = 0

   for epoch in range(EPOCHS):
       print("\n----- epoch: {}, lr: {} -----".format(
           epoch, optimizer.param_groups[0]["lr"]))

       # train for one epoch
       start_time = time.time()
       last_top1_acc, train_loss, train_acc = train(train_loader, epoch, model, optimizer, criterion)
       elapsed_time = time.time() - start_time
       print('==> {:.2f} seconds to train this epoch\n'.format(
           elapsed_time))
       
       # LOSS FOR EARLY STOPPING
       valid_loss, valid_acc = valid(val_loader, epoch, model, optimizer, criterion)
       """
       if early_stop_check == PATIENCE:
         print('\n******* Early Stopping *******\n')
         break
       """
       if valid_loss < best_valid_loss:
         early_stop_check = 0
         best_valid_loss = valid_loss
         torch.save(model.state_dict(), SAVEPATH+'earlystop_check_best.pth')
         print(f'\n\t## SAVE valid_loss: {valid_loss:.3f} | valid_acc: {valid_acc:.3f} ##')
       else:
         early_stop_check += 1

       # learning rate scheduling
       scheduler.step()

       # Save model each epoch
       torch.save(model.state_dict(), SAVEPATH+'earlystop_check.pth')

       print(f'\n\t==Epoch: {epoch + 1:02} | Epoch Time: {elapsed_time:.2f}s==')
       print(f'\t==Train Loss: {train_loss:.3f} | Train acc: {train_acc:.3f}==')
       print(f'\t==Valid Loss: {valid_loss:.3f} | Valid acc: {valid_acc:.3f}==\n')

   print(f"Last Top-1 Accuracy: {last_top1_acc}")
   print(f"Number of parameters: {pytorch_total_params}")


def train(train_loader, epoch, model, optimizer, criterion):
   batch_time = AverageMeter('Time', ':6.3f')
   data_time = AverageMeter('Data', ':6.3f')
   losses = AverageMeter('Loss', ':.4e')
   top1 = AverageMeter('Acc@1', ':6.2f')
   top5 = AverageMeter('Acc@5', ':6.2f')
   progress = ProgressMeter(len(train_loader), batch_time, data_time, losses,
                            top1, top5, prefix="Epoch: [{}]".format(epoch))
   
   # LOSS FOR EARLYSTOPPPING
   total_loss = 0
   iter_num = 0
   train_acc = 0

   # switch to train mode
   model.train()

   end = time.time()
   for i, (input, target) in enumerate(train_loader):
       # measure data loading time
       data_time.update(time.time() - end)

       input = input.cuda()
       target = target.cuda()

       # compute output
       output = model(input)
       loss = criterion(output, target)

       # measure accuracy and record loss, accuracy
       acc1, acc5 = accuracy(output, target, topk=(1, 5))
       losses.update(loss.item(), input.size(0))
       top1.update(acc1[0].item(), input.size(0))
       top5.update(acc5[0].item(), input.size(0))

       # compute gradient and do SGD step
       optimizer.zero_grad()
       loss.backward()
       optimizer.step()

       # LOSS FOR EARLYSTOPPING
       total_loss += loss.item()
       iter_num += 1
       train_acc += acc1.item()

       # measure elapsed time
       batch_time.update(time.time() - end)
       end = time.time()

       if i % PRINTFREQ == 0:
           progress.print(i)

   print('=> Acc@1 {top1.avg:.3f} Acc@5 {top5.avg:.3f}'
         .format(top1=top1, top5=top5))
   return top1.avg, total_loss / iter_num, train_acc / iter_num

def valid(val_loader, epoch, model, optimizer, criterion):
   # LOSS FOR EARLYSTOPPPING
   total_loss = 0
   iter_num = 0
   val_acc = 0

   with torch.no_grad():
     for i, (input, target) in enumerate(val_loader):
       input = input.cuda()
       target = target.cuda()

       output = model(input)
       loss = criterion(output, target)
       acc1 = accuracy(output, target, topk=(1,))
       
       total_loss += loss.item()
       iter_num += 1
       val_acc += acc1[0].item()

     return total_loss / iter_num, val_acc / iter_num


if __name__ == "__main__":
    main()

Number of parameters: 1604682


14.4%IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

96.1%IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

100.0%

Extracting /home/dhk1349/바탕화면/dataset/cifar10/cifar-10-python.tar.gz to /home/dhk1349/바탕화면/dataset/cifar10/
Files already downloaded and verified

----- epoch: 0, lr: 0.1 -----
Epoch: [0][    0/12500]	Time  0.177 ( 0.177)	Data  0.042 ( 0.042)	Loss 2.3638e+00 (2.3638e+00)	Acc@1  25.00 ( 25.00)	Acc@5  50.00 ( 50.00)
Epoch: [0][   10/12500]	Time  0.007 ( 0.023)	Data  0.001 ( 0.005)	Loss 2.6257e+00 (1.0522e+01)	Acc@1  25.00 ( 15.91)	Acc@5 100.00 ( 61.36)
Epoch: [0][   20/12500]	Time  0.007 ( 0.015)	Data  0.001 ( 0.003)	Loss 1.8179e+00 (6.6076e+00)	Acc@1  25.00 ( 15.48)	Acc@5  75.00 ( 58.33)
Epoch: [0][   30/12500]	Time  0.007 ( 0.013)	Data  0.001 ( 0.002)	Loss 2.4151e+00 (5.2785e+00)	Acc@1   0.00 ( 13.71)	Acc@5  50.00 ( 57.26)
Epoch: [0][   40/12500]	Time  0.008 ( 0.011)	Data  0.001 ( 0.002)	Loss 2.2735e+00 (4.5657e+00)	Acc@1  25.00 ( 14.63)	Acc@5  50.00 ( 54.88)
Epoch: [0][   50/12500]	Time  0.007 ( 0.011)	Data  0.001 ( 0.002)	Loss 2.3900e+00 (4.1386e+00)	Acc@1   0.00 ( 14.22)	Acc@5  75.0

Epoch: [0][  580/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.5281e+00 (2.4620e+00)	Acc@1   0.00 ( 14.67)	Acc@5  50.00 ( 59.12)
Epoch: [0][  590/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 1.9865e+00 (2.4557e+00)	Acc@1  25.00 ( 14.72)	Acc@5  75.00 ( 59.39)
Epoch: [0][  600/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.0315e+00 (2.4545e+00)	Acc@1  25.00 ( 14.73)	Acc@5  75.00 ( 59.40)
Epoch: [0][  610/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.4814e+00 (2.4514e+00)	Acc@1   0.00 ( 14.69)	Acc@5  75.00 ( 59.37)
Epoch: [0][  620/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 1.7936e+00 (2.4477e+00)	Acc@1  50.00 ( 14.81)	Acc@5 100.00 ( 59.34)
Epoch: [0][  630/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 1.7758e+00 (2.4440e+00)	Acc@1  50.00 ( 15.06)	Acc@5  75.00 ( 59.43)
Epoch: [0][  640/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2520e+00 (2.4423e+00)	Acc@1  25.00 ( 15.09)	Acc@5  75.00 ( 59.56)
Epoch: [0][  650/12500]	Tim

Epoch: [0][ 1170/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 1.7522e+00 (2.3662e+00)	Acc@1  50.00 ( 15.65)	Acc@5  75.00 ( 61.42)
Epoch: [0][ 1180/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.0245e+00 (2.3652e+00)	Acc@1  25.00 ( 15.73)	Acc@5  75.00 ( 61.43)
Epoch: [0][ 1190/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3839e+00 (2.3649e+00)	Acc@1   0.00 ( 15.62)	Acc@5  75.00 ( 61.46)
Epoch: [0][ 1200/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3163e+00 (2.3635e+00)	Acc@1   0.00 ( 15.63)	Acc@5  75.00 ( 61.57)
Epoch: [0][ 1210/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2241e+00 (2.3632e+00)	Acc@1  50.00 ( 15.59)	Acc@5  50.00 ( 61.58)
Epoch: [0][ 1220/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.1824e+00 (2.3622e+00)	Acc@1  25.00 ( 15.64)	Acc@5  75.00 ( 61.59)
Epoch: [0][ 1230/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.1686e+00 (2.3612e+00)	Acc@1   0.00 ( 15.64)	Acc@5  75.00 ( 61.62)
Epoch: [0][ 1240/12500]	Tim

...

Epoch: [27][ 6510/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2436e+00 (2.3542e+00)	Acc@1   0.00 (  9.84)	Acc@5  75.00 ( 50.01)
Epoch: [27][ 6520/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.4644e+00 (2.3542e+00)	Acc@1   0.00 (  9.84)	Acc@5  25.00 ( 50.00)
Epoch: [27][ 6530/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3837e+00 (2.3542e+00)	Acc@1   0.00 (  9.85)	Acc@5  75.00 ( 49.99)
Epoch: [27][ 6540/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2949e+00 (2.3543e+00)	Acc@1  25.00 (  9.85)	Acc@5  25.00 ( 49.98)
Epoch: [27][ 6550/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.5968e+00 (2.3543e+00)	Acc@1   0.00 (  9.85)	Acc@5  25.00 ( 49.98)
Epoch: [27][ 6560/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2620e+00 (2.3543e+00)	Acc@1  25.00 (  9.85)	Acc@5  50.00 ( 49.97)
Epoch: [27][ 6570/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3996e+00 (2.3543e+00)	Acc@1   0.00 (  9.86)	Acc@5  50.00 ( 49.97)
Epoch: [27][ 6580/12

Epoch: [27][ 7110/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.4615e+00 (2.3542e+00)	Acc@1   0.00 (  9.92)	Acc@5  50.00 ( 50.11)
Epoch: [27][ 7120/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.4090e+00 (2.3542e+00)	Acc@1   0.00 (  9.93)	Acc@5  75.00 ( 50.11)
Epoch: [27][ 7130/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.5531e+00 (2.3542e+00)	Acc@1   0.00 (  9.93)	Acc@5  25.00 ( 50.11)
Epoch: [27][ 7140/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2219e+00 (2.3542e+00)	Acc@1  25.00 (  9.93)	Acc@5  75.00 ( 50.11)
Epoch: [27][ 7150/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2915e+00 (2.3542e+00)	Acc@1   0.00 (  9.92)	Acc@5  50.00 ( 50.10)
Epoch: [27][ 7160/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3468e+00 (2.3542e+00)	Acc@1  50.00 (  9.93)	Acc@5  50.00 ( 50.10)
Epoch: [27][ 7170/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.7237e+00 (2.3543e+00)	Acc@1   0.00 (  9.92)	Acc@5   0.00 ( 50.10)
Epoch: [27][ 7180/12

Epoch: [27][ 7710/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.0613e+00 (2.3543e+00)	Acc@1  25.00 (  9.94)	Acc@5 100.00 ( 50.05)
Epoch: [27][ 7720/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.9084e+00 (2.3543e+00)	Acc@1   0.00 (  9.94)	Acc@5  25.00 ( 50.05)
Epoch: [27][ 7730/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2401e+00 (2.3544e+00)	Acc@1  25.00 (  9.94)	Acc@5  75.00 ( 50.05)
Epoch: [27][ 7740/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2589e+00 (2.3544e+00)	Acc@1  25.00 (  9.95)	Acc@5  50.00 ( 50.04)
Epoch: [27][ 7750/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.5124e+00 (2.3544e+00)	Acc@1   0.00 (  9.95)	Acc@5  25.00 ( 50.04)
Epoch: [27][ 7760/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3559e+00 (2.3544e+00)	Acc@1  25.00 (  9.95)	Acc@5  25.00 ( 50.02)
Epoch: [27][ 7770/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.4139e+00 (2.3544e+00)	Acc@1   0.00 (  9.95)	Acc@5  25.00 ( 50.02)
Epoch: [27][ 7780/12

Epoch: [27][ 8310/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3796e+00 (2.3549e+00)	Acc@1  25.00 (  9.98)	Acc@5  50.00 ( 49.96)
Epoch: [27][ 8320/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.5955e+00 (2.3547e+00)	Acc@1   0.00 (  9.99)	Acc@5  50.00 ( 49.99)
Epoch: [27][ 8330/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3644e+00 (2.3547e+00)	Acc@1   0.00 (  9.99)	Acc@5  50.00 ( 50.01)
Epoch: [27][ 8340/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.6566e+00 (2.3547e+00)	Acc@1   0.00 ( 10.00)	Acc@5  25.00 ( 50.00)
Epoch: [27][ 8350/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.7019e+00 (2.3547e+00)	Acc@1   0.00 ( 10.00)	Acc@5  25.00 ( 50.00)
Epoch: [27][ 8360/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2769e+00 (2.3546e+00)	Acc@1  50.00 ( 10.00)	Acc@5  75.00 ( 50.02)
Epoch: [27][ 8370/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3224e+00 (2.3547e+00)	Acc@1  50.00 ( 10.01)	Acc@5  50.00 ( 50.02)
Epoch: [27][ 8380/12

Epoch: [27][ 8910/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2320e+00 (2.3546e+00)	Acc@1  25.00 ( 10.00)	Acc@5  75.00 ( 50.01)
Epoch: [27][ 8920/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.3635e+00 (2.3546e+00)	Acc@1   0.00 ( 10.01)	Acc@5  25.00 ( 50.01)
Epoch: [27][ 8930/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.5133e+00 (2.3545e+00)	Acc@1   0.00 ( 10.00)	Acc@5  25.00 ( 50.02)
Epoch: [27][ 8940/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2883e+00 (2.3545e+00)	Acc@1   0.00 ( 10.00)	Acc@5  50.00 ( 50.02)
Epoch: [27][ 8950/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.2982e+00 (2.3545e+00)	Acc@1  25.00 ( 10.00)	Acc@5  50.00 ( 50.02)
Epoch: [27][ 8960/12500]	Time  0.007 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.5056e+00 (2.3546e+00)	Acc@1   0.00 ( 10.00)	Acc@5   0.00 ( 50.01)
Epoch: [27][ 8970/12500]	Time  0.008 ( 0.008)	Data  0.001 ( 0.001)	Loss 2.4639e+00 (2.3545e+00)	Acc@1   0.00 ( 10.00)	Acc@5  50.00 ( 50.03)
Epoch: [27][ 8980/12